<a href="https://colab.research.google.com/github/CaptainDilawar/AI-Powered-Image-Video-Composition-Tool/blob/main/Image_Video_Composition.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
# @title Step 1: Install a Compatible Set of Libraries
!pip install -q rembg==2.0.50 moviepy==1.0.3 opencv-python==4.8.0.76 numpy==1.23.5 Pillow==9.5.0

print("✅ All libraries installed successfully!")
print("\n🔴 IMPORTANT: Please restart the runtime now before proceeding.")

In [ ]:
# @title Step 2: Upload Product Image and Video Template

from google.colab import files
import os

# Clean up previous uploads if they exist
if os.path.exists('/content/input_image.png'): os.remove('/content/input_image.png')
if os.path.exists('/content/template_video.mp4'): os.remove('/content/template_video.mp4')


print("Please upload one product image AND one video template.")
uploaded = files.upload()

input_image_path = None
template_video_path = None

image_extensions = ['.png', '.jpg', '.jpeg']
video_extensions = ['.mp4', '.mov', '.avi']

for filename, content in uploaded.items():
    ext = os.path.splitext(filename)[1].lower()
    if ext in image_extensions and not input_image_path:
        # Save the uploaded image to a consistent path
        input_image_path = f"/content/input_image{ext}"
        with open(input_image_path, 'wb') as f:
            f.write(content)
        print(f"✅ Saved image as: {input_image_path}")
    elif ext in video_extensions and not template_video_path:
        # Save the uploaded video to a consistent path
        template_video_path = f"/content/template_video.mp4"
        with open(template_video_path, 'wb') as f:
            f.write(content)
        print(f"✅ Saved video as: {template_video_path}")

# --- Validation ---
if not input_image_path or not template_video_path:
    print("\n❌ Error: Please run this cell again and make sure you upload ONE image file and ONE video file.")
else:
    print("\n✅ Files uploaded and saved successfully. You can now run the next cell.")

Please upload one product image AND one video template.


Saving WhatsApp Image 2025-07-02 at 5.18.14 PM - Copy.jpeg to WhatsApp Image 2025-07-02 at 5.18.14 PM - Copy.jpeg
Saving 0_Bubbles_Underwater_1080x1920.mp4 to 0_Bubbles_Underwater_1080x1920.mp4
✅ Saved image as: /content/input_image.jpeg
✅ Saved video as: /content/template_video.mp4

✅ Files uploaded and saved successfully. You can now run the next cell.


In [ ]:
# @title Step 3: Run the AI Pipeline (with Interactive Controls)

#@markdown ---
#@markdown ### 🎬 Animation Controls
#@markdown Adjust these sliders and re-run this cell to change the final video.
sway_amount_degrees = 6 #@param {type:"slider", min:0, max:45, step:1}
product_size_percentage = 30 #@param {type:"slider", min:10, max:100, step:1}
#@markdown ---


import os
import cv2
import numpy as np
from PIL import Image
from rembg import remove
from moviepy.editor import VideoFileClip, ImageSequenceClip, CompositeVideoClip
import math
import io

# --- Configuration ---
OUTPUT_VIDEO_PATH = "/content/final_output.mp4"

# Animation settings are now taken from the sliders above
VIDEO_DURATION_SECONDS = 5
FPS = 30

# --- Pipeline Functions ---

def step1_remove_background(image_path):
    """Takes an image path, removes background, and ensures output is RGBA."""
    print("Step 1: Removing background...")
    with open(image_path, "rb") as f_in:
        input_bytes = f_in.read()
    output_bytes = remove(input_bytes)
    image_pil = Image.open(io.BytesIO(output_bytes))
    if image_pil.mode != 'RGBA':
        image_pil = image_pil.convert('RGBA')
    return image_pil

def step2_create_animation_frames(image_pil, duration, fps, max_tilt_degrees):
    """Generates animation frames with a 'sway' effect."""
    print(f"Step 2: Generating animation frames with a {max_tilt_degrees}-degree sway...")
    image_np = np.array(image_pil)
    h, w, _ = image_np.shape
    total_frames = duration * fps
    animated_frames = []
    src_points = np.float32([[0, 0], [w, 0], [0, h], [w, h]])

    for i in range(total_frames):
        angle_rad = math.radians(max_tilt_degrees * math.sin(2 * math.pi * i / total_frames))
        top_shift = w / 2 * math.tan(angle_rad)
        dst_points = np.float32([[top_shift, 0], [w - top_shift, 0], [0, h], [w, h]])
        matrix = cv2.getPerspectiveTransform(src_points, dst_points)
        warped_frame = cv2.warpPerspective(image_np, matrix, (w, h), borderMode=cv2.BORDER_CONSTANT, borderValue=(0,0,0,0))
        animated_frames.append(warped_frame)
    return animated_frames

def step3_composite_video(frames, video_template_path, output_path, fps, product_size):
    """Overlays frames onto the background video."""
    print("Step 3: Compositing final video...")
    background_clip = VideoFileClip(video_template_path).set_duration(VIDEO_DURATION_SECONDS)

    animation_frames_rgb = [frame[:, :, :3] for frame in frames]
    animation_frames_alpha = [frame[:, :, 3:4] / 255.0 for frame in frames]

    animation_clip = ImageSequenceClip(animation_frames_rgb, fps=fps)
    mask_clip = ImageSequenceClip(animation_frames_alpha, fps=fps, ismask=True)

    animation_clip = animation_clip.set_mask(mask_clip)

    # Use the product_size parameter from the slider
    animation_clip = animation_clip.resize(height=background_clip.h * (product_size / 100))

    final_clip = CompositeVideoClip([
        background_clip,
        animation_clip.set_position(('center', 'center'))
    ])

    final_clip.write_videofile(output_path, codec='libx264', audio_codec='aac', logger=None, preset='ultrafast', threads=2)
    print(f"\n🎉 Success! Video saved to '{output_path}'")

# --- Main Execution Block ---
if 'input_image_path' in locals() and 'template_video_path' in locals() and input_image_path and template_video_path:
    try:
        # Pass the slider values into the functions
        bg_removed_image = step1_remove_background(input_image_path)
        frames_list = step2_create_animation_frames(bg_removed_image, VIDEO_DURATION_SECONDS, FPS, sway_amount_degrees)
        step3_composite_video(frames_list, template_video_path, OUTPUT_VIDEO_PATH, FPS, product_size_percentage)
    except Exception as e:
        print(f"\n❌ An error occurred during the pipeline: {e}")
        import traceback
        traceback.print_exc()
else:
    print("\n❌ Error: Input files not found. Please run the 'Upload' cell (Step 2) successfully before running this cell.")

  if event.key is 'enter':



Step 1: Removing background...


100%|███████████████████████████████████████| 176M/176M [00:00<00:00, 65.6GB/s]


Step 2: Generating animation frames with a 6-degree sway...
Step 3: Compositing final video...

🎉 Success! Video saved to '/content/final_output.mp4'


In [ ]:
# @title Step 4: Display and Download the Final Video

from IPython.display import HTML, display
from base64 import b64encode

# Check if the output video file exists
if os.path.exists(OUTPUT_VIDEO_PATH):
  mp4 = open(OUTPUT_VIDEO_PATH, 'rb').read()
  data_url = "data:video/mp4;base64," + b64encode(mp4).decode()

  display(HTML(f"""
  <h3>Your Final Video:</h3>
  <video width=600 controls autoplay loop>
        <source src="{data_url}" type="video/mp4">
  </video>
  """))

  print("\nDownloading the video file automatically...")
  # files.download(OUTPUT_VIDEO_PATH)

else:
    print("❌ Output video not found. Please make sure the previous cell (Step 3) ran without errors.")